In [1]:
import os
import sys
import numpy as np
import gc
from utils.utils import process_radar_file, process_video_file, save_radar_maps, save_video_frames, process_video_file_wide_angle

base_path = "/Volumes/HIP_BACKUP/MEMOIRE/Code/MyDB2"

source_data_path = "/Volumes/HIP_BACKUP/MEMOIRE/DATA_COLLECTION"
radar_data_path = os.path.join(source_data_path, "Radar")
video_data_path = os.path.join(source_data_path, "Video")

In [4]:
### ANCIEN DATASET ###
#input_videos_filenames = [f"Videos/my_video-{i}.mkv" for i in [4,5,6,7,8,9,13,14]]
#input_radar_raw_filenames = ["RawDataDL/04-2people.npz", "RawDataDL/05-pleindegens.npz", "RawDataDL/06-pleindegens2.npz", "RawDataDL/07-crowd.npz", "RawDataDL/08-crowdagain.npz", "RawDataDL/09-crowd3.npz", "RawDataDL/13-CROWD.npz", "RawDataDL/14-few.npz"]
#exp_names = [f"Exp{i}" for i in [1,2,3,4,5,6,7,8]]

### CALIBRATION ###
#input_videos_filenames = [f"{video_data_path}/calibration.MOV"]
#input_radar_raw_filenames  = [f"{radar_data_path}/calibration1.npz"]
#exp_names = ["Calibration"]


### NOUVEAU DATASET ###
n_exp = np.arange(25, 51)

input_videos_filenames = [f"{video_data_path}/exp{i}.MOV" for i in n_exp]
input_radar_raw_filenames  = [f"{radar_data_path}/exp{i}.npz" for i in n_exp]
exp_names = [f"NewExp{i}" for i in n_exp]


In [5]:
crop_index = None

if crop_index == None: crop_index = len(input_videos_filenames)

for f, (input_video_filename, input_radar_raw_filename) in enumerate(zip(input_videos_filenames[:crop_index], input_radar_raw_filenames[:crop_index])):
    print(f"Processing {input_video_filename} and {input_radar_raw_filename}")

    radar_data = process_radar_file(input_radar_raw_filename, saveMagn=True, savePhase=True)
    timestamps = radar_data['timestamps']
    video_data = process_video_file(input_video_filename, timestamps, saveFrames=True)

    n_radar_maps = len(radar_data['magnitudes'])
    n_labels = len(video_data['labels'])

    max_values = []
    min_values = []

    for i in range(min(n_radar_maps, n_labels)):
        save_radar_maps(radar_data['magnitudes'][i], i, video_data['labels'][i], f"{base_path}/{exp_names[f]}/RadarMagnitudes")
        save_radar_maps(radar_data['phases'][i], i, video_data['labels'][i], f"{base_path}/{exp_names[f]}/RadarPhases")
        save_video_frames(video_data['frames'][i], i, video_data['labels'][i], f"{base_path}/{exp_names[f]}/VideoFrames")
        max_values.append(radar_data['magnitudes'][i].max())
        min_values.append(radar_data['magnitudes'][i].min())

    # Save the labels as a numpy array into a new folder
    os.makedirs(f"{base_path}/{exp_names[f]}/Labels", exist_ok=True)
    np.save(f"{base_path}/{exp_names[f]}/Labels/labels.npy", np.array(video_data['labels']))

    # Save max values as a numpy array into a new folder
    os.makedirs(f"{base_path}/{exp_names[f]}/MaxValues", exist_ok=True)
    np.save(f"{base_path}/{exp_names[f]}/MaxValues/max_values.npy", np.array(max_values))

    # Save min values as a numpy array into a new folder
    os.makedirs(f"{base_path}/{exp_names[f]}//MinValues", exist_ok=True)
    np.save(f"{base_path}/{exp_names[f]}/MinValues/min_values.npy", np.array(min_values))

    # ✅ Libération de la mémoire après chaque vidéo
    del radar_data
    del video_data
    del timestamps
    del max_values
    del min_values

    gc.collect()  # Forcer la récupération de mémoire



Processing /Volumes/HIP_BACKUP/MEMOIRE/DATA_COLLECTION/Video/exp25.MOV and /Volumes/HIP_BACKUP/MEMOIRE/DATA_COLLECTION/Radar/exp25.npz
 Frame iD  999/1000

0: 384x640 14 persons, 352.4ms
Speed: 16.3ms preprocess, 352.4ms inference, 22.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 289.7ms
Speed: 1.3ms preprocess, 289.7ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 287.8ms
Speed: 1.5ms preprocess, 287.8ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 298.6ms
Speed: 1.2ms preprocess, 298.6ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 337.0ms
Speed: 1.4ms preprocess, 337.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 309.8ms
Speed: 1.5ms preprocess, 309.8ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 14 persons, 316.2ms
Speed: 1.4ms preprocess, 316.2m

In [4]:
# Save the max_values from the radar data
